In [3]:
import requests
import json
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
import re
import csv
import matplotlib.pyplot as plt
%matplotlib inline

pd.set_option('display.max_columns', 500)

## Bring in previously-pulled reports for Material Handlers, Assemblers, Warehouse job listings for TN and TX

Concat vertically into one dataframe

In [4]:
mat_hand_tn = pd.read_json('data/material_handler_tn.json')
mat_hand_tn

recordsFiltered  recordsTotal  \
0                1819          1819   
1                1819          1819   
2                1819          1819   
3                1819          1819   
4                1819          1819   
...               ...           ...   
1812             1819          1819   
1813             1819          1819   
1814             1819          1819   
1815             1819          1819   
1816             1819          1819   

                                                   data  draw  success  \
0     {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
1     {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
2     {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
3     {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
4     {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
...                                                 ...   ...      ...   
1812  {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
1813  {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
1814  {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
1815  {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
1816  {'keyword': 'Material Handler', 'zipcity': Non...     0     True   

      elapsedSeconds  results  
0             17.544  success  
1             17.544  success  
2             17.544  success  
3             17.544  success  
4             17.544  success  
...              ...      ...  
1812          17.544  success  
1813          17.544  success  
1814          17.544  success  
1815          17.544  success  
1816          17.544  success  

[1817 rows x 7 columns]

In [5]:
assembler_tn = pd.read_json('data/assembler_tn.json')
assembler_tn.data[0]

{'keyword': 'Assembler',
 'zipcity': None,
 'jobdescription_snippet': ' ... <span class="highlight_keyword">ASSEMBLER</span> - EARN $14/HOUR We are hiring immediately for an <span class="highlight_keyword">Assembler</span> to join our production department in the Knoxville area. The <span class="highlight_keyword">Assembler</span> will be responsible for packaging and assembling products for distribution while working as part of a team. The ideal candidate for the <span class="highlight_keyword">Assembler</span> position will have experience in a production setting and will be able to stand, twist, and move at a face pace during each shift. We are hiring over 50 assembly/production individuals for an immediate start. If you are interested in this position, apply today! <span class="highlight_keyword">Assembler</span> Pay, Schedule, and Location - Starting at $14/hour - 1st, 2nd, and 3rd shift opportunities available - Located in Knoxville, TN <span class="highlight_keyword">Assembler</

In [6]:
warehouse_tn1 = pd.read_json('data/warehouse_tn.json')
warehouse_tn1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4000 entries, 0 to 3999
Data columns (total 7 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   recordsFiltered  4000 non-null   int64  
 1   recordsTotal     4000 non-null   int64  
 2   data             4000 non-null   object 
 3   draw             4000 non-null   int64  
 4   success          4000 non-null   bool   
 5   elapsedSeconds   4000 non-null   float64
 6   results          4000 non-null   object 
dtypes: bool(1), float64(1), int64(3), object(2)
memory usage: 191.5+ KB


In [7]:
warehouse_tn1

recordsFiltered  recordsTotal  \
0                7237          7237   
1                7237          7237   
2                7237          7237   
3                7237          7237   
4                7237          7237   
...               ...           ...   
3995             7237          7237   
3996             7237          7237   
3997             7237          7237   
3998             7237          7237   
3999             7237          7237   

                                                   data  draw  success  \
0     {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
1     {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
2     {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
3     {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
4     {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
...                                                 ...   ...      ...   
3995  {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
3996  {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
3997  {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
3998  {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
3999  {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   

      elapsedSeconds  results  
0             35.818  success  
1             35.818  success  
2             35.818  success  
3             35.818  success  
4             35.818  success  
...              ...      ...  
3995          35.818  success  
3996          35.818  success  
3997          35.818  success  
3998          35.818  success  
3999          35.818  success  

[4000 rows x 7 columns]

In [8]:
# Removing 2nd TN warehouse report because keeps returning 0 records, and already have 4000
# warehouse_tn2 = pd.read_json('data/warehouse_tn2.json')
# warehouse_tn2.info()

In [9]:
mat_hand_tx = pd.read_json('data/material_handler_tx.json')
mat_hand_tx

recordsFiltered  recordsTotal  \
0                5616          5616   
1                5616          5616   
2                5616          5616   
3                5616          5616   
4                5616          5616   
...               ...           ...   
3995             5616          5616   
3996             5616          5616   
3997             5616          5616   
3998             5616          5616   
3999             5616          5616   

                                                   data  draw  success  \
0     {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
1     {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
2     {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
3     {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
4     {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
...                                                 ...   ...      ...   
3995  {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
3996  {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
3997  {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
3998  {'keyword': 'Material Handler', 'zipcity': Non...     0     True   
3999  {'keyword': 'Material Handler', 'zipcity': Non...     0     True   

      elapsedSeconds  results  
0             40.833  success  
1             40.833  success  
2             40.833  success  
3             40.833  success  
4             40.833  success  
...              ...      ...  
3995          40.833  success  
3996          40.833  success  
3997          40.833  success  
3998          40.833  success  
3999          40.833  success  

[4000 rows x 7 columns]

In [10]:
assembler_tx = pd.read_json('data/assembler_tx.json')
assembler_tx

recordsFiltered  recordsTotal  \
0                2868          2868   
1                2868          2868   
2                2868          2868   
3                2868          2868   
4                2868          2868   
...               ...           ...   
2863             2868          2868   
2864             2868          2868   
2865             2868          2868   
2866             2868          2868   
2867             2868          2868   

                                                   data  draw  success  \
0     {'keyword': 'Assembler', 'zipcity': None, 'job...     0     True   
1     {'keyword': 'Assembler', 'zipcity': None, 'job...     0     True   
2     {'keyword': 'Assembler', 'zipcity': None, 'job...     0     True   
3     {'keyword': 'Assembler', 'zipcity': None, 'job...     0     True   
4     {'keyword': 'Assembler', 'zipcity': None, 'job...     0     True   
...                                                 ...   ...      ...   
2863  {'keyword': 'Assembler', 'zipcity': None, 'job...     0     True   
2864  {'keyword': 'Assembler', 'zipcity': None, 'job...     0     True   
2865  {'keyword': 'Assembler', 'zipcity': None, 'job...     0     True   
2866  {'keyword': 'Assembler', 'zipcity': None, 'job...     0     True   
2867  {'keyword': 'Assembler', 'zipcity': None, 'job...     0     True   

      elapsedSeconds  results  
0             18.804  success  
1             18.804  success  
2             18.804  success  
3             18.804  success  
4             18.804  success  
...              ...      ...  
2863          18.804  success  
2864          18.804  success  
2865          18.804  success  
2866          18.804  success  
2867          18.804  success  

[2868 rows x 7 columns]

In [11]:
warehouse_tx1 = pd.read_json('data/warehouse_tx.json')
warehouse_tx1

recordsFiltered  recordsTotal  \
0                5563          5563   
1                5563          5563   
2                5563          5563   
3                5563          5563   
4                5563          5563   
...               ...           ...   
2995             5563          5563   
2996             5563          5563   
2997             5563          5563   
2998             5563          5563   
2999             5563          5563   

                                                   data  draw  success  \
0     {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
1     {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
2     {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
3     {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
4     {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
...                                                 ...   ...      ...   
2995  {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
2996  {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
2997  {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
2998  {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   
2999  {'keyword': 'Warehouse', 'zipcity': None, 'job...     0     True   

      elapsedSeconds  results  
0             33.011  success  
1             33.011  success  
2             33.011  success  
3             33.011  success  
4             33.011  success  
...              ...      ...  
2995          33.011  success  
2996          33.011  success  
2997          33.011  success  
2998          33.011  success  
2999          33.011  success  

[3000 rows x 7 columns]

In [12]:
warehouse_tx1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3000 entries, 0 to 2999
Data columns (total 7 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   recordsFiltered  3000 non-null   int64  
 1   recordsTotal     3000 non-null   int64  
 2   data             3000 non-null   object 
 3   draw             3000 non-null   int64  
 4   success          3000 non-null   bool   
 5   elapsedSeconds   3000 non-null   float64
 6   results          3000 non-null   object 
dtypes: bool(1), float64(1), int64(3), object(2)
memory usage: 143.7+ KB


In [13]:
warehouse_tx2 = pd.read_json('data/warehouse_tx2.json')
warehouse_tx2.data[1]

{'keyword': 'Warehouse',
 'zipcity': None,
 'jobdescription_snippet': ' ... <span class="highlight_keyword">Warehouse</span> Operations contributes to Cardinal Health <span class="highlight_keyword">Warehouse</span> Operations is responsible for performing/controlling a combination of manual or automated tasks necessary for the receipt, storage, and shipment of product. This may include functions of receiving, picking, packing, shipping, staging, transporting, storage, delivery, etc. Also responsible for the efficient flow of products from the point of product receipt from vendors to the shipment of products (via prescribed service parameters) to a variety of internal and external customers. Qualifications - High School Diploma/GED preferred - Good written communication skills - 1-2 years experience - Proficient in Microsoft office preferred What is expected of you and others at this level - Applies acquired knowledge and skills to complete standard tasks - Readily learns and applies n

In [14]:
warehouse_tx2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1369 entries, 0 to 1368
Data columns (total 7 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   recordsFiltered  1369 non-null   int64  
 1   recordsTotal     1369 non-null   int64  
 2   data             1369 non-null   object 
 3   draw             1369 non-null   int64  
 4   success          1369 non-null   bool   
 5   elapsedSeconds   1369 non-null   float64
 6   results          1369 non-null   object 
dtypes: bool(1), float64(1), int64(3), object(2)
memory usage: 65.6+ KB


In [15]:
first_concat = pd.concat([assembler_tn, assembler_tx], ignore_index=True)
#axis=1

In [16]:
second_concat = pd.concat([mat_hand_tn, mat_hand_tx], ignore_index=True)

In [17]:
third_concat = pd.concat([warehouse_tx1, warehouse_tx2], ignore_index=True)

In [18]:
fourth_concat = pd.concat([warehouse_tn1], ignore_index=True)

#warehouse_tn2

In [19]:
all_df = [first_concat, second_concat, third_concat, fourth_concat]
final_df = pd.concat(all_df, ignore_index=True)

In [20]:
final_df.shape

(18237, 7)

Update codes below with new combined blue_collar df

In [21]:
type(final_df)

pandas.core.frame.DataFrame

In [22]:
final_df.columns

Index(['recordsFiltered', 'recordsTotal', 'data', 'draw', 'success',
       'elapsedSeconds', 'results'],
      dtype='object')

In [23]:
final_df = final_df.drop(columns=['recordsFiltered', 'recordsTotal','draw', 'success', 'elapsedSeconds', 'results'])

In [24]:
final_df.data[0]

{'keyword': 'Assembler',
 'zipcity': None,
 'jobdescription_snippet': ' ... <span class="highlight_keyword">ASSEMBLER</span> - EARN $14/HOUR We are hiring immediately for an <span class="highlight_keyword">Assembler</span> to join our production department in the Knoxville area. The <span class="highlight_keyword">Assembler</span> will be responsible for packaging and assembling products for distribution while working as part of a team. The ideal candidate for the <span class="highlight_keyword">Assembler</span> position will have experience in a production setting and will be able to stand, twist, and move at a face pace during each shift. We are hiring over 50 assembly/production individuals for an immediate start. If you are interested in this position, apply today! <span class="highlight_keyword">Assembler</span> Pay, Schedule, and Location - Starting at $14/hour - 1st, 2nd, and 3rd shift opportunities available - Located in Knoxville, TN <span class="highlight_keyword">Assembler</

In [25]:
final_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18237 entries, 0 to 18236
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   data    18237 non-null  object
dtypes: object(1)
memory usage: 142.6+ KB


In [26]:
final_df.shape

(18237, 1)

In [27]:
final_df.dropna(inplace = True) 

In [28]:
final_df.shape

(18237, 1)

In [29]:
job_list = final_df["data"].tolist()

In [30]:
job_list

[{'keyword': 'Assembler',
  'zipcity': None,
  'jobdescription_snippet': ' ... <span class="highlight_keyword">ASSEMBLER</span> - EARN $14/HOUR We are hiring immediately for an <span class="highlight_keyword">Assembler</span> to join our production department in the Knoxville area. The <span class="highlight_keyword">Assembler</span> will be responsible for packaging and assembling products for distribution while working as part of a team. The ideal candidate for the <span class="highlight_keyword">Assembler</span> position will have experience in a production setting and will be able to stand, twist, and move at a face pace during each shift. We are hiring over 50 assembly/production individuals for an immediate start. If you are interested in this position, apply today! <span class="highlight_keyword">Assembler</span> Pay, Schedule, and Location - Starting at $14/hour - 1st, 2nd, and 3rd shift opportunities available - Located in Knoxville, TN <span class="highlight_keyword">Assemble

In [31]:
type(job_list)

list

In [32]:
job_titles = [d["jobtitle"] for d in job_list]
city = [d["city"] for d in job_list]
snippet = [d["jobdescription_snippet"] for d in job_list]
job_descriptions = [d["jobdescription"] for d in job_list]
min_sal = [d.get('minsal') for d in job_list]  
max_sal = [d.get('maxsal') for d in job_list]  



In [33]:
job_descriptions

['Job Description Hello First Name, We are excited to have received your application at Accurate Personnel. Please give me a call back today regarding this position. Thank you, Recruiter HIRING IMMEDIATELY: <span class="highlight_keyword">ASSEMBLER</span> - EARN $14/HOUR We are hiring immediately for an <span class="highlight_keyword">Assembler</span> to join our production department in the Knoxville area. The <span class="highlight_keyword">Assembler</span> will be responsible for packaging and assembling products for distribution while working as part of a team. The ideal candidate for the <span class="highlight_keyword">Assembler</span> position will have experience in a production setting and will be able to stand, twist, and move at a face pace during each shift. We are hiring over 50 assembly/production individuals for an immediate start. If you are interested in this position, apply today! <span class="highlight_keyword">Assembler</span> Pay, Schedule, and Location - Starting a

In [34]:
city

['Knoxville',
 'Knoxville',
 'Covington',
 'PORTLAND',
 'Cookeville',
 'Dyersburg',
 'Morristown',
 'Morristown',
 'Lawrenceburg',
 'Tullahoma',
 'Parsons',
 'Parsons',
 'FRANKLIN',
 'Knoxville',
 'PELHAM',
 'Tullahoma',
 'Memphis',
 'Tullahoma',
 'Ooltewah',
 'Athens',
 'Gallatin',
 'Covington',
 'Gallatin',
 'Johnson City',
 'Johnson City',
 'Pelham',
 'Crossville',
 'Dayton',
 'Portland',
 'Fayetteville',
 'Dickson',
 'Vonore',
 'Sevierville',
 'Spring Hill',
 'LEBANON                            ',
 'Spring Hill',
 'Chattanooga',
 'Dyersburg',
 'Columbia',
 'Decherd',
 'Jackson',
 'Jackson',
 'Athens',
 'Manchester',
 'Greeneville',
 'Greenbrier',
 'Sharon',
 'Clarksville',
 'Union City',
 'Vonore',
 'Vonore',
 'Vonore',
 'Brownsville',
 'Knoxville',
 'Knoxville',
 'Clarksville',
 'Collierville',
 'Sharon',
 'MEMPHIS',
 'Tullahoma',
 'Pelham',
 'MORRISTOWN',
 'Newbern',
 'Clarksville',
 'Clarksville',
 'Portland',
 'Portland',
 'Rogersville',
 'Greeneville',
 'Clinton',
 'Portland',

In [35]:
snippet

[' ... <span class="highlight_keyword">ASSEMBLER</span> - EARN $14/HOUR We are hiring immediately for an <span class="highlight_keyword">Assembler</span> to join our production department in the Knoxville area. The <span class="highlight_keyword">Assembler</span> will be responsible for packaging and assembling products for distribution while working as part of a team. The ideal candidate for the <span class="highlight_keyword">Assembler</span> position will have experience in a production setting and will be able to stand, twist, and move at a face pace during each shift. We are hiring over 50 assembly/production individuals for an immediate start. If you are interested in this position, apply today! <span class="highlight_keyword">Assembler</span> Pay, Schedule, and Location - Starting at $14/hour - 1st, 2nd, and 3rd shift opportunities available - Located in Knoxville, TN <span class="highlight_keyword">Assembler</span> Duties and Responsibilities - Package and assemble products for

In [36]:
min_sal

[None,
 None,
 '$12.92',
 '$13.00',
 '$9.00',
 None,
 '$10.25',
 '$12.50',
 None,
 None,
 None,
 None,
 None,
 '$11.00',
 '$12.00',
 None,
 None,
 None,
 None,
 '$15.00',
 None,
 '$12.92',
 '$12.50',
 '$12.00',
 None,
 '$12.25',
 None,
 '$12.00',
 None,
 None,
 None,
 '$12.60',
 '$11.00',
 '$15.50',
 None,
 '$12.50',
 '$11.50',
 None,
 '$15.50',
 None,
 '$15.00',
 '$15.00',
 None,
 '$12.50',
 None,
 None,
 None,
 None,
 None,
 '$12.60',
 '$12.60',
 '$12.60',
 '$15.50',
 '$13.00',
 None,
 None,
 '$16.14',
 None,
 '$13.00',
 None,
 '$12.00',
 '$14.08',
 '$9.50',
 None,
 None,
 None,
 '$16.50',
 None,
 None,
 '$11.00',
 None,
 None,
 None,
 None,
 None,
 '$10.00',
 None,
 None,
 '$12.00',
 '$11.50',
 '$11.00',
 None,
 '$12.00',
 '$12.00',
 '$15.00',
 '$10.00',
 None,
 '$14.50',
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 '$13.00',
 None,
 None,
 None,
 None,
 '$17.00',
 '$15.00',
 '$17.00',
 '$19.50',
 '$12.00',
 

In [37]:
max_sal

[None,
 None,
 '$16.43',
 '$15.00',
 '$14.50',
 None,
 '$13.50',
 '$13.50',
 None,
 None,
 None,
 None,
 None,
 '$12.00',
 '$13.72',
 None,
 None,
 None,
 None,
 '$17.00',
 None,
 '$16.43',
 '$13.00',
 '$12.60',
 None,
 '$13.97',
 None,
 '$12.00',
 None,
 None,
 None,
 '$16.10',
 '$14.03',
 '$15.50',
 None,
 '$15.50',
 '$16.50',
 None,
 '$16.00',
 None,
 '$16.00',
 '$16.00',
 None,
 '$12.50',
 None,
 None,
 None,
 None,
 None,
 '$16.10',
 '$16.10',
 '$16.10',
 '$15.50',
 '$13.00',
 None,
 None,
 '$16.14',
 None,
 '$14.50',
 None,
 '$12.25',
 '$15.79',
 '$9.50',
 None,
 None,
 None,
 '$17.25',
 None,
 None,
 '$12.00',
 None,
 None,
 None,
 None,
 None,
 '$12.01',
 None,
 None,
 '$12.50',
 '$11.50',
 '$11.00',
 None,
 '$13.00',
 '$12.50',
 '$15.00',
 '$10.00',
 None,
 '$14.50',
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 '$13.00',
 None,
 None,
 None,
 None,
 '$17.00',
 '$15.00',
 '$17.00',
 '$19.50',
 '$13.00',


Unable to do regex at this time, will try to create df with narrowed columns and nltk on that

In [39]:
bluecollar = pd.DataFrame()
bluecollar['title'] = job_titles
bluecollar['job_snippet'] = snippet
bluecollar['location'] = city
bluecollar['full_description'] = job_descriptions
bluecollar['min_pay'] = min_sal
bluecollar['max_pay'] = max_sal

print(bluecollar)

                                                   title  \
0       <span class="highlight_keyword">Assembler</span>   
1       <span class="highlight_keyword">Assembler</span>   
2      <span class="highlight_keyword">Assembler</spa...   
3      <span class="highlight_keyword">Assembler</spa...   
4      Manufacturing <span class="highlight_keyword">...   
...                                                  ...   
18232                         Inventory Associate - 0406   
18233                         Inventory Associate - 0406   
18234                         Inventory Associate - 0406   
18235                         Inventory Associate - 0406   
18236                         Inventory Associate - 0406   

                                             job_snippet      location  \
0       ... <span class="highlight_keyword">ASSEMBLER...     Knoxville   
1       ... <span class="highlight_keyword">ASSEMBLER...     Knoxville   
2       ... <span class="highlight_keyword">Assembler... 

Remove the brackets with "highlight keyword" and "span", and \\n

In [40]:
bluecollar['title'] = bluecollar['title'].apply(lambda x: re.sub(r'<.*?>','', str(x)))

In [41]:
bluecollar['job_snippet'] = bluecollar['job_snippet'].apply(lambda x: re.sub(r'<.*?>','', str(x)))

In [42]:
bluecollar['full_description'] =  bluecollar['full_description'].apply(lambda x: re.sub(r'<.*?>','', str(x)))

In [43]:
bluecollar['full_description'] =  bluecollar['full_description'].apply(lambda x: re.sub(r'\\n','', str(x)))

In [44]:
bluecollar['job_snippet'] =  bluecollar['job_snippet'].apply(lambda x: re.sub(r'\\n','', str(x)))

In [45]:
bluecollar

title  \
0                       Assembler   
1                       Assembler   
2                    Assembler I    
3       Assembler and Fabricator    
4        Manufacturing Assembler    
...                           ...   
18232  Inventory Associate - 0406   
18233  Inventory Associate - 0406   
18234  Inventory Associate - 0406   
18235  Inventory Associate - 0406   
18236  Inventory Associate - 0406   

                                             job_snippet      location  \
0       ... ASSEMBLER - EARN $14/HOUR We are hiring i...     Knoxville   
1       ... ASSEMBLER - EARN $14/HOUR We are hiring i...     Knoxville   
2       ... Assembler I Job Code: 100006 Salary Grade...     Covington   
3       ... Assembler/Fabricators will be trained to:...      PORTLAND   
4      General warehouse assembly line. We have avail...    Cookeville   
...                                                  ...           ...   
18232   ... warehouse physically counting merchandise...     Oak Ridge   
18233   ... warehouse physically counting merchandise...     Maryville   
18234   ... warehouse physically counting merchandise...  Jonesborough   
18235   ... warehouse physically counting merchandise...     Kingsport   
18236   ... warehouse physically counting merchandise...  Johnson City   

                                        full_description min_pay max_pay  
0      Job Description Hello First Name, We are excit...    None    None  
1      Job Description HIRING IMMEDIATELY: ASSEMBLER ...    None    None  
2       Position Description Hourly/Production Job Ti...  $12.92  $16.43  
3      PRODUCTION – ENTRY LEVEL – NO EXPERIENCE NECES...  $13.00  $15.00  
4      General warehouse assembly line. We have avail...   $9.00  $14.50  
...                                                  ...     ...     ...  
18232  We are pleased to announce a $200 Sign-on Bonu...    None    None  
18233  We are pleased to announce a $200 Sign-on Bonu...    None    None  
18234  We are pleased to announce a $200 Sign-on Bonu...    None    None  
18235  We are pleased to announce a $200 Sign-on Bonu...    None    None  
18236  We are pleased to announce a $200 Sign-on Bonu...    None    None  

[18237 rows x 6 columns]

Now, identify keywords that could imply criticality of finding talent, search the job snippet and job description fields, and count the number of times the keywords appear

First run the keywords against "job snippet"

In [49]:
import string
import nltk
nltk.download('punkt')
nltk.download('stopwords')
from nltk.corpus import stopwords
from nltk.tokenize import RegexpTokenizer
from nltk.stem.wordnet import WordNetLemmatizer

def preprocess_text(job_snippet):
    job_snippet = job_snippet.lower() # To lower
    translator = str.maketrans('', '', string.punctuation)
    job_snippet = job_snippet.translate(translator) # Removing punctuation
    filtered_words = [w for w in job_snippet.split() if w not in stopwords.words('english')] # Removing stopwords from the tokenized text
    return ' '.join(filtered_words) # returns the resulting list as a string

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\daily\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\daily\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [50]:
KEYWORDS = ['bonus', 'bonuses','sign-on bonus', 'incentive', 'pay increase', 'no minimum education requirement','training','will consider arrest and conviction records' ]

def count_keywords(job_snippet):
    counts = {}
    prep = preprocess_text(job_snippet)
    for kw in KEYWORDS:
        counts[kw] = prep.count(kw)
    return counts

In [51]:
bluecollar['occur_snippet'] = bluecollar['job_snippet'].apply(count_keywords)

And then run the words against the "full_description"

In [52]:
def preprocess_text(full_description):
    full_description = full_description.lower() # To lower
    translator = str.maketrans('', '', string.punctuation)
    full_description = full_description.translate(translator) # Removing punctuation
    filtered_words = [w for w in full_description.split() if w not in stopwords.words('english')] # Removing stopwords from the tokenized text
    return ' '.join(filtered_words) # We return the resulting list as a string

In [53]:
KEYWORDS = ['bonus', 'bonuses','sign-on bonus', 'incentive', 'pay increase', 'no minimum education requirement','training', 'will consider arrest and conviction records' ]

def count_keywords(full_description):
    counts = {}
    prep = preprocess_text(full_description)
    for kw in KEYWORDS:
        counts[kw] = prep.count(kw)
    return counts

In [54]:
bluecollar['occur_full_desc'] = bluecollar['full_description'].apply(count_keywords)

In [55]:
bluecollar

title  \
0                       Assembler   
1                       Assembler   
2                    Assembler I    
3       Assembler and Fabricator    
4        Manufacturing Assembler    
...                           ...   
18232  Inventory Associate - 0406   
18233  Inventory Associate - 0406   
18234  Inventory Associate - 0406   
18235  Inventory Associate - 0406   
18236  Inventory Associate - 0406   

                                             job_snippet      location  \
0       ... ASSEMBLER - EARN $14/HOUR We are hiring i...     Knoxville   
1       ... ASSEMBLER - EARN $14/HOUR We are hiring i...     Knoxville   
2       ... Assembler I Job Code: 100006 Salary Grade...     Covington   
3       ... Assembler/Fabricators will be trained to:...      PORTLAND   
4      General warehouse assembly line. We have avail...    Cookeville   
...                                                  ...           ...   
18232   ... warehouse physically counting merchandise...     Oak Ridge   
18233   ... warehouse physically counting merchandise...     Maryville   
18234   ... warehouse physically counting merchandise...  Jonesborough   
18235   ... warehouse physically counting merchandise...     Kingsport   
18236   ... warehouse physically counting merchandise...  Johnson City   

                                        full_description min_pay max_pay  \
0      Job Description Hello First Name, We are excit...    None    None   
1      Job Description HIRING IMMEDIATELY: ASSEMBLER ...    None    None   
2       Position Description Hourly/Production Job Ti...  $12.92  $16.43   
3      PRODUCTION – ENTRY LEVEL – NO EXPERIENCE NECES...  $13.00  $15.00   
4      General warehouse assembly line. We have avail...   $9.00  $14.50   
...                                                  ...     ...     ...   
18232  We are pleased to announce a $200 Sign-on Bonu...    None    None   
18233  We are pleased to announce a $200 Sign-on Bonu...    None    None   
18234  We are pleased to announce a $200 Sign-on Bonu...    None    None   
18235  We are pleased to announce a $200 Sign-on Bonu...    None    None   
18236  We are pleased to announce a $200 Sign-on Bonu...    None    None   

                                           occur_snippet  \
0      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
1      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
2      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
3      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
4      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
...                                                  ...   
18232  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
18233  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
18234  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
18235  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
18236  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   

                                         occur_full_desc  
0      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...  
1      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...  
2      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...  
3      {'bonus': 1, 'bonuses': 1, 'sign-on bonus': 0,...  
4      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...  
...                                                  ...  
18232  {'bonus': 1, 'bonuses': 0, 'sign-on bonus': 0,...  
18233  {'bonus': 1, 'bonuses': 0, 'sign-on bonus': 0,...  
18234  {'bonus': 1, 'bonuses': 0, 'sign-on bonus': 0,...  
18235  {'bonus': 1, 'bonuses': 0, 'sign-on bonus': 0,...  
18236  {'bonus': 1, 'bonuses': 0, 'sign-on bonus': 0,...  

[18237 rows x 8 columns]

In [60]:
full_desc_incent = bluecollar.occur_full_desc.tolist()

In [61]:
pd.DataFrame(full_desc_incent)

bonus  bonuses  sign-on bonus  incentive  pay increase  \
0          0        0              0          0             0   
1          0        0              0          0             0   
2          0        0              0          0             0   
3          1        1              0          0             0   
4          0        0              0          0             0   
...      ...      ...            ...        ...           ...   
18232      1        0              0          0             0   
18233      1        0              0          0             0   
18234      1        0              0          0             0   
18235      1        0              0          0             0   
18236      1        0              0          0             0   

       no minimum education requirement  training  \
0                                     0         0   
1                                     0         0   
2                                     0         1   
3                                     0         1   
4                                     0         0   
...                                 ...       ...   
18232                                 0         0   
18233                                 0         0   
18234                                 0         0   
18235                                 0         0   
18236                                 0         0   

       will consider arrest and conviction records  
0                                                0  
1                                                0  
2                                                0  
3                                                0  
4                                                0  
...                                            ...  
18232                                            0  
18233                                            0  
18234                                            0  
18235                                            0  
18236                                            0  

[18237 rows x 8 columns]

In [62]:
snippet_incent = bluecollar.occur_snippet.tolist()

In [64]:
pd.DataFrame(snippet_incent)

bonus  bonuses  sign-on bonus  incentive  pay increase  \
0          0        0              0          0             0   
1          0        0              0          0             0   
2          0        0              0          0             0   
3          0        0              0          0             0   
4          0        0              0          0             0   
...      ...      ...            ...        ...           ...   
18232      0        0              0          0             0   
18233      0        0              0          0             0   
18234      0        0              0          0             0   
18235      0        0              0          0             0   
18236      0        0              0          0             0   

       no minimum education requirement  training  \
0                                     0         0   
1                                     0         0   
2                                     0         0   
3                                     0         0   
4                                     0         0   
...                                 ...       ...   
18232                                 0         0   
18233                                 0         0   
18234                                 0         0   
18235                                 0         0   
18236                                 0         0   

       will consider arrest and conviction records  
0                                                0  
1                                                0  
2                                                0  
3                                                0  
4                                                0  
...                                            ...  
18232                                            0  
18233                                            0  
18234                                            0  
18235                                            0  
18236                                            0  

[18237 rows x 8 columns]

In [70]:
type(bluecollar)

pandas.core.frame.DataFrame

In [73]:
bluecollar2 = pd.concat([bluecollar,pd.DataFrame(snippet_incent)], axis=1)

In [84]:
bluecollar2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18237 entries, 0 to 18236
Data columns (total 16 columns):
 #   Column                                       Non-Null Count  Dtype 
---  ------                                       --------------  ----- 
 0   title                                        18237 non-null  object
 1   job_snippet                                  18237 non-null  object
 2   location                                     18237 non-null  object
 3   full_description                             18237 non-null  object
 4   min_pay                                      4218 non-null   object
 5   max_pay                                      4192 non-null   object
 6   occur_snippet                                18237 non-null  object
 7   occur_full_desc                              18237 non-null  object
 8   bonus                                        18237 non-null  int64 
 9   bonuses                                      18237 non-null  int64 
 10  sign-on bo

In [87]:
bluecollar2 = bluecollar2.rename(columns = {'bonus':'snippet_bonus', 'bonuses':'snippet_bonuses', 'sign-on bonus':'snippet_signon',
                             'incentive':'snippet_incentive', 'pay increase': 'snippet_payincrease', 
                              'no minimum education requirement':'snippet_nomined', 'training':'snippet_training',
                             'will consider arrest and conviction records':'snippet_arrestok'})
bluecollar2

title  \
0                       Assembler   
1                       Assembler   
2                    Assembler I    
3       Assembler and Fabricator    
4        Manufacturing Assembler    
...                           ...   
18232  Inventory Associate - 0406   
18233  Inventory Associate - 0406   
18234  Inventory Associate - 0406   
18235  Inventory Associate - 0406   
18236  Inventory Associate - 0406   

                                             job_snippet      location  \
0       ... ASSEMBLER - EARN $14/HOUR We are hiring i...     Knoxville   
1       ... ASSEMBLER - EARN $14/HOUR We are hiring i...     Knoxville   
2       ... Assembler I Job Code: 100006 Salary Grade...     Covington   
3       ... Assembler/Fabricators will be trained to:...      PORTLAND   
4      General warehouse assembly line. We have avail...    Cookeville   
...                                                  ...           ...   
18232   ... warehouse physically counting merchandise...     Oak Ridge   
18233   ... warehouse physically counting merchandise...     Maryville   
18234   ... warehouse physically counting merchandise...  Jonesborough   
18235   ... warehouse physically counting merchandise...     Kingsport   
18236   ... warehouse physically counting merchandise...  Johnson City   

                                        full_description min_pay max_pay  \
0      Job Description Hello First Name, We are excit...    None    None   
1      Job Description HIRING IMMEDIATELY: ASSEMBLER ...    None    None   
2       Position Description Hourly/Production Job Ti...  $12.92  $16.43   
3      PRODUCTION – ENTRY LEVEL – NO EXPERIENCE NECES...  $13.00  $15.00   
4      General warehouse assembly line. We have avail...   $9.00  $14.50   
...                                                  ...     ...     ...   
18232  We are pleased to announce a $200 Sign-on Bonu...    None    None   
18233  We are pleased to announce a $200 Sign-on Bonu...    None    None   
18234  We are pleased to announce a $200 Sign-on Bonu...    None    None   
18235  We are pleased to announce a $200 Sign-on Bonu...    None    None   
18236  We are pleased to announce a $200 Sign-on Bonu...    None    None   

                                           occur_snippet  \
0      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
1      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
2      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
3      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
4      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
...                                                  ...   
18232  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
18233  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
18234  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
18235  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
18236  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   

                                         occur_full_desc  snippet_bonus  \
0      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   
1      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   
2      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   
3      {'bonus': 1, 'bonuses': 1, 'sign-on bonus': 0,...              0   
4      {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   
...                                                  ...            ...   
18232  {'bonus': 1, 'bonuses': 0, 'sign-on bonus': 0,...              0   
18233  {'bonus': 1, 'bonuses': 0, 'sign-on bonus': 0,...              0   
18234  {'bonus': 1, 'bonuses': 0, 'sign-on bonus': 0,...              0   
18235  {'bonus': 1, 'bonuses': 0, 'sign-on bonus': 0,...              0   
18236  {'bonus': 1, 'bonuses': 0, 'sign-on bonus': 0,...              0   

       snippet_bonuses  snippet_signon  snippet_incentive  \
0                    0               0                  0   
1                    0               

In [88]:
bluecollar3 = pd.concat([bluecollar2, pd.DataFrame(full_desc_incent)], axis=1)

In [89]:
bluecollar3.head()

title  \
0                  Assembler   
1                  Assembler   
2               Assembler I    
3  Assembler and Fabricator    
4   Manufacturing Assembler    

                                         job_snippet    location  \
0   ... ASSEMBLER - EARN $14/HOUR We are hiring i...   Knoxville   
1   ... ASSEMBLER - EARN $14/HOUR We are hiring i...   Knoxville   
2   ... Assembler I Job Code: 100006 Salary Grade...   Covington   
3   ... Assembler/Fabricators will be trained to:...    PORTLAND   
4  General warehouse assembly line. We have avail...  Cookeville   

                                    full_description min_pay max_pay  \
0  Job Description Hello First Name, We are excit...    None    None   
1  Job Description HIRING IMMEDIATELY: ASSEMBLER ...    None    None   
2   Position Description Hourly/Production Job Ti...  $12.92  $16.43   
3  PRODUCTION – ENTRY LEVEL – NO EXPERIENCE NECES...  $13.00  $15.00   
4  General warehouse assembly line. We have avail...   $9.00  $14.50   

                                       occur_snippet  \
0  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
1  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
2  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
3  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
4  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   

                                     occur_full_desc  snippet_bonus  \
0  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   
1  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   
2  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   
3  {'bonus': 1, 'bonuses': 1, 'sign-on bonus': 0,...              0   
4  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   

   snippet_bonuses  snippet_signon  snippet_incentive  snippet_payincrease  \
0                0               0                  0                    0   
1                0               0                  0                    0   
2                0               0                  0                    0   
3                0               0                  0                    0   
4                0               0                  0                    0   

   snippet_nomined  snippet_training  snippet_arrestok  bonus  bonuses  \
0                0                 0                 0      0        0   
1                0                 0                 0      0        0   
2                0                 0                 0      0        0   
3                0                 0                 0      1        1   
4                0                 0                 0      0        0   

   sign-on bonus  incentive  pay increase  no minimum education requirement  \
0              0          0             0                                 0   
1              0          0             0                                 0   
2              0          0             0                                 0   
3              0          0             0                                 0   
4              0          0             0                                 0   

   training  will consider arrest and conviction records  
0         0                                            0  
1         0                                            0  
2         1                                            0  
3         1                                            0  
4         0                                            0

In [93]:
bluecollar3 = bluecollar3.rename(columns = {'bonus':'desc_bonus', 'bonuses':'desc_bonuses', 'sign-on bonus':'desc_signon',
                             'incentive':'desc_incentive', 'pay increase':'desc_payincrease', 
                              'no minimum education requirement':'desc_nomined', 'training':'desc_training',
                             'will consider arrest and conviction records':'desc_arrestok'})
bluecollar3.head(3)

title                                        job_snippet   location  \
0     Assembler   ... ASSEMBLER - EARN $14/HOUR We are hiring i...  Knoxville   
1     Assembler   ... ASSEMBLER - EARN $14/HOUR We are hiring i...  Knoxville   
2  Assembler I    ... Assembler I Job Code: 100006 Salary Grade...  Covington   

                                    full_description min_pay max_pay  \
0  Job Description Hello First Name, We are excit...    None    None   
1  Job Description HIRING IMMEDIATELY: ASSEMBLER ...    None    None   
2   Position Description Hourly/Production Job Ti...  $12.92  $16.43   

                                       occur_snippet  \
0  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
1  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   
2  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...   

                                     occur_full_desc  snippet_bonus  \
0  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   
1  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   
2  {'bonus': 0, 'bonuses': 0, 'sign-on bonus': 0,...              0   

   snippet_bonuses  snippet_signon  snippet_incentive  snippet_payincrease  \
0                0               0                  0                    0   
1                0               0                  0                    0   
2                0               0                  0                    0   

   snippet_nomined  snippet_training  snippet_arrestok  desc_bonus  \
0                0                 0                 0           0   
1                0                 0                 0           0   
2                0                 0                 0           0   

   desc_bonuses  desc_signon  desc_incentive  desc_payincrease  desc_nomined  \
0             0            0               0                 0             0   
1             0            0               0                 0             0   
2             0            0               0                 0             0   

   desc_training  desc_arrestok  
0              0              0  
1              0              0  
2              1              0

In [91]:
# Count the number of occurences between the job snippet and the full job description
bluecollar3.describe()

snippet_bonus  snippet_bonuses  snippet_signon  snippet_incentive  \
count   18237.000000     18237.000000         18237.0       18237.000000   
mean        0.077151         0.021056             0.0           0.018150   
std         0.408189         0.161207             0.0           0.139915   
min         0.000000         0.000000             0.0           0.000000   
25%         0.000000         0.000000             0.0           0.000000   
50%         0.000000         0.000000             0.0           0.000000   
75%         0.000000         0.000000             0.0           0.000000   
max         7.000000         3.000000             0.0           4.000000   

       snippet_payincrease  snippet_nomined  snippet_training  \
count         18237.000000          18237.0      18237.000000   
mean              0.004606              0.0          0.158195   
std               0.069314              0.0          0.540355   
min               0.000000              0.0          0.000000   
25%               0.000000              0.0          0.000000   
50%               0.000000              0.0          0.000000   
75%               0.000000              0.0          0.000000   
max               2.000000              0.0          7.000000   

       snippet_arrestok    desc_bonus  desc_bonuses  desc_signon  \
count           18237.0  18237.000000  18237.000000      18237.0   
mean                0.0      0.168339      0.050282          0.0   
std                 0.0      0.591821      0.253825          0.0   
min                 0.0      0.000000      0.000000          0.0   
25%                 0.0      0.000000      0.000000          0.0   
50%                 0.0      0.000000      0.000000          0.0   
75%                 0.0      0.000000      0.000000          0.0   
max                 0.0     12.000000     12.000000          0.0   

       desc_incentive  desc_payincrease  desc_nomined  desc_training  \
count    18237.000000      18237.000000       18237.0   18237.000000   
mean         0.047650          0.008390           0.0       0.456599   
std          0.226021          0.099823           0.0       0.917133   
min          0.000000          0.000000           0.0       0.000000   
25%          0.000000          0.000000           0.0       0.000000   
50%          0.000000          0.000000           0.0       0.000000   
75%          0.000000          0.000000           0.0       1.000000   
max          4.000000          3.000000           0.0      19.000000   

       desc_arrestok  
count        18237.0  
mean             0.0  
std              0.0  
min              0.0  
25%              0.0  
50%              0.0  
75%              0.0  
max              0.0

In [98]:
sum_incent = bluecollar3.drop(columns = ['title', 'job_snippet', 'location', 'full_description', 'min_pay', 'max_pay',
                                        'occur_snippet', 'occur_full_desc'])
sum_incent.sum(axis=0)



snippet_bonus          1407
snippet_bonuses         384
snippet_signon            0
snippet_incentive       331
snippet_payincrease      84
snippet_nomined           0
snippet_training       2885
snippet_arrestok          0
desc_bonus             3070
desc_bonuses            917
desc_signon               0
desc_incentive          869
desc_payincrease        153
desc_nomined              0
desc_training          8327
desc_arrestok             0
dtype: int64

In [ ]:
#'eduexpdesc': 'No Minimum Education Requirement'
# 'jobtypedesc': 'Contract'
# 'jobtitle':
# 'city':
# 'minsal': '$14.00',
# 'maxsal': '$14.00',
# 'employer': 
# 'jobdescription':
# 'cwsource': 'AdeccoUSA', 
# 'aliasdesc': 'Recruiter',

In [ ]:
#keys = ['jobtitle', 'city', 'employer', 'cwsource', 'jobtypedesc', 'minsal', 'maxsal', 'jobdescription', 'eduexpdesc' ]


In [ ]:
#Use extractall to get all the key value pairs in long format, and transform it so the keys goes as the column headers

# (Mat_Hand.data.str.extractall("([^,]+?):(?:\s{2}([^,]+))?")
#    .reset_index(level=1, drop=True)
#    .set_index(0, append=True)[1]
#    .unstack(level=1))